In [1]:
%matplotlib inline
import tensorflow as tf
import numpy as np
import os
import scipy.io
import glob
from glob import glob
import scipy.misc as misc
import warnings
from distutils.version import LooseVersion
import helper
import project_tests as tests
import skimage
from matplotlib import pyplot as plt

In [2]:
# Check TensorFlow Version
assert LooseVersion(tf.__version__) >= LooseVersion('1.0'), 'Please use TensorFlow version 1.0 or newer.  You are using {}'.format(tf.__version__)
print('TensorFlow Version: {}'.format(tf.__version__))

TensorFlow Version: 1.8.0


In [3]:
# Check for a GPU
if not tf.test.gpu_device_name():
  warnings.warn('No GPU found. Please use a GPU to train your neural network.')
else:
  print('Default GPU Device: {}'.format(tf.test.gpu_device_name()))

Default GPU Device: /device:GPU:0


In [4]:
DATA_DIRECTORY = './data'
RUNS_DIRECTORY = './runs'
VGG_PATH = './data/vgg'
TRAINING_DATA_DIRECTORY ='./data/data_liquid/training'
TESTING_DATA_DIRECTORY = './data/data_liquid/testing'

dirs = [x[0] for x in os.walk(TESTING_DATA_DIRECTORY)]
TESTING_DIRECTORIES = dirs[1:]

dirs = [x[0] for x in os.walk(TRAINING_DATA_DIRECTORY)]
TRAINING_DIRECTORIES = dirs[1:]

# Get the number of images altogether
x = 0
for d in dirs:
    ip = glob(os.path.join(d, 'data*.png'))
    x += len(ip)    
NUMBER_OF_IMAGES = x # 11192 #len(glob.glob('./data/data_liquid/testing/image_2/*.*'))

In [5]:
NUMBER_OF_CLASSES = 2
IMAGE_SHAPE = (480, 640)

EPOCHS = 10
BATCH_SIZE = 1

LEARNING_RATE = 0.0001
DROPOUT = 0.75

In [6]:
correct_label = tf.placeholder(tf.float32, [None, IMAGE_SHAPE[0], IMAGE_SHAPE[1], NUMBER_OF_CLASSES])
learning_rate = tf.placeholder(tf.float32)
keep_prob = tf.placeholder(tf.float32)

In [7]:
# Used for plotting to visualize if our training is going well given parameters
all_training_losses = []

In [8]:
def load_vgg(sess, vgg_path):
  """
  Load Pretrained VGG Model into TensorFlow.
  sess: TensorFlow Session
  vgg_path: Path to vgg folder, containing "variables/" and "saved_model.pb"
  return: Tuple of Tensors from VGG model (image_input, keep_prob, layer3, layer4, layer7)
  """
  # load the model and weights
  model = tf.saved_model.loader.load(sess, ['vgg16'], vgg_path)

  # Get Tensors to be returned from graph
  graph = tf.get_default_graph()
  image_input = graph.get_tensor_by_name('image_input:0')
  keep_prob = graph.get_tensor_by_name('keep_prob:0')
  layer3 = graph.get_tensor_by_name('layer3_out:0')
  layer4 = graph.get_tensor_by_name('layer4_out:0')
  layer7 = graph.get_tensor_by_name('layer7_out:0')

  return image_input, keep_prob, layer3, layer4, layer7

In [9]:
def conv_1x1(layer, layer_name):
  """ Return the output of a 1x1 convolution of a layer """
  return tf.layers.conv2d(inputs = layer,
                          filters =  NUMBER_OF_CLASSES,
                          kernel_size = (1, 1),
                          strides = (1, 1),
                          name = layer_name)

In [10]:
def upsample(layer, k, s, layer_name):
  """ Return the output of transpose convolution given kernel_size k and strides s """
  # See: http://deeplearning.net/software/theano/tutorial/conv_arithmetic.html#transposed-convolution-arithmetic
  return tf.layers.conv2d_transpose(inputs = layer,
                                    filters = NUMBER_OF_CLASSES,
                                    kernel_size = (k, k),
                                    strides = (s, s),
                                    padding = 'same',
                                    name = layer_name)

In [11]:
def layers(vgg_layer3_out, vgg_layer4_out, vgg_layer7_out, num_classes = NUMBER_OF_CLASSES):
  """
  Create the layers for a fully convolutional network.  Build skip-layers using the vgg layers.
  vgg_layerX_out: TF Tensor for VGG Layer X output
  num_classes: Number of classes to classify
  return: The Tensor for the last layer of output
  """

  # Use a shorter variable name for simplicity
  layer3, layer4, layer7 = vgg_layer3_out, vgg_layer4_out, vgg_layer7_out

  # Apply a 1x1 convolution to encoder layers
  layer3x = conv_1x1(layer = layer3, layer_name = "layer3conv1x1")
  layer4x = conv_1x1(layer = layer4, layer_name = "layer4conv1x1")
  layer7x = conv_1x1(layer = layer7, layer_name = "layer7conv1x1")
 
  # Add decoder layers to the network with skip connections and upsampling
  # Note: the kernel size and strides are the same as the example in Udacity Lectures
  #       Semantic Segmentation Scene Understanding Lesson 10-9: FCN-8 - Decoder
  decoderlayer1 = upsample(layer = layer7x, k = 4, s = 2, layer_name = "decoderlayer1")
  decoderlayer2 = tf.add(decoderlayer1, layer4x, name = "decoderlayer2")
  decoderlayer3 = upsample(layer = decoderlayer2, k = 4, s = 2, layer_name = "decoderlayer3")
  decoderlayer4 = tf.add(decoderlayer3, layer3x, name = "decoderlayer4")
  decoderlayer_output = upsample(layer = decoderlayer4, k = 16, s = 8, layer_name = "decoderlayer_output")

  return decoderlayer_output

In [12]:
def layers_verbose(vgg_layer3_out, vgg_layer4_out, vgg_layer7_out, num_classes = NUMBER_OF_CLASSES):

  # Use a shorter variable name for simplicity
  layer3, layer4, layer7 = vgg_layer3_out, vgg_layer4_out, vgg_layer7_out

  # Apply a 1x1 convolution to encoder layers
  layer3x = conv_1x1(layer = layer3, layer_name = "layer3conv1x1")
  layer4x = conv_1x1(layer = layer4, layer_name = "layer4conv1x1")
  layer7x = conv_1x1(layer = layer7, layer_name = "layer7conv1x1")
 
  decoderlayer1 = upsample(layer = layer7x, k = 4, s = 2, layer_name = "decoderlayer1")
  decoderlayer2 = tf.add(decoderlayer1, layer4x, name = "decoderlayer2")
  decoderlayer3 = upsample(layer = decoderlayer2, k = 4, s = 2, layer_name = "decoderlayer3")
  decoderlayer4 = tf.add(decoderlayer3, layer3x, name = "decoderlayer4")
  decoderlayer_output = upsample(layer = decoderlayer4, k = 16, s = 8, layer_name = "decoderlayer_output")

  return layer3, layer4, layer7, layer3x, layer4x, layer7x, \
         decoderlayer1, decoderlayer2, decoderlayer3, decoderlayer4, decoderlayer_output


In [13]:
def optimize(nn_last_layer, correct_label, learning_rate, num_classes = NUMBER_OF_CLASSES):
  """
  Build the TensorFLow loss and optimizer operations.
  nn_last_layer: TF Tensor of the last layer in the neural network
  correct_label: TF Placeholder for the correct label image
  learning_rate: TF Placeholder for the learning rate
  num_classes: Number of classes to classify
  return: Tuple of (logits, train_op, cross_entropy_loss)
  """
  # reshape 4D tensors to 2D
  # Each row represents a pixel, each column a class
  logits = tf.reshape(nn_last_layer, (-1, num_classes))
  class_labels = tf.reshape(correct_label, (-1, num_classes))

  # The cross_entropy_loss is the cost which we are trying to minimize to yield higher accuracy
  cross_entropy = tf.nn.softmax_cross_entropy_with_logits(logits = logits, labels = class_labels)
  cross_entropy_loss = tf.reduce_mean(cross_entropy)

  # The model implements this operation to find the weights/parameters that would yield correct pixel labels
  train_op = tf.train.AdamOptimizer(learning_rate).minimize(cross_entropy_loss)

  return logits, train_op, cross_entropy_loss

In [14]:
def train_nn(sess, epochs, batch_size, get_batches_fn, train_op,
             cross_entropy_loss, input_image,
             correct_label, keep_prob, learning_rate, saver):
  """
  Train neural network and print out the loss during training.
  sess: TF Session
  epochs: Number of epochs
  batch_size: Batch size
  get_batches_fn: Function to get batches of training data.  Call using get_batches_fn(batch_size)
  train_op: TF Operation to train the neural network
  cross_entropy_loss: TF Tensor for the amount of loss
  input_image: TF Placeholder for input images
  correct_label: TF Placeholder for label images
  keep_prob: TF Placeholder for dropout keep probability
  learning_rate: TF Placeholder for learning rate
  """

  for epoch in range(EPOCHS):
    
    losses, i = [], 0
    
    for images, labels in get_batches_fn(BATCH_SIZE):
        
      i += 1
    
      feed = { input_image: images,
               correct_label: labels,
               keep_prob: DROPOUT,
               learning_rate: LEARNING_RATE }
        
      _, partial_loss = sess.run([train_op, cross_entropy_loss], feed_dict = feed)
      
      print("---> iteration: ", i, " partial loss:", partial_loss)
      losses.append(partial_loss)
      
      if i % 100 == 0:
        # Save model
        saver.save(sess, "./model_10epochs")  
          
    training_loss = sum(losses) / len(losses)
    all_training_losses.append(training_loss)
    
    print("------------------")
    print("epoch: ", epoch + 1, " of ", EPOCHS, "training loss: ", training_loss)
    print("------------------")

In [15]:
def run_tests():
  tests.test_layers(layers)
  tests.test_optimize(optimize)
  tests.test_for_kitti_dataset(DATA_DIRECTORY)
  tests.test_train_nn(train_nn)

In [16]:
def run():
  print("NUMBER OF IMAGES:", NUMBER_OF_IMAGES)

  # download vgg model
  helper.maybe_download_pretrained_vgg(DATA_DIRECTORY)

  # A function to get batches
  get_batches_fn = helper.gen_batch_function(TRAINING_DIRECTORIES, IMAGE_SHAPE)

 
  
  with tf.Session() as session:
        
    # Returns the three layers, keep probability and input layer from the vgg architecture
    image_input, keep_prob, layer3, layer4, layer7 = load_vgg(session, VGG_PATH)

    # The resulting network architecture, adding a decoder on top of the given vgg model
    model_output = layers(layer3, layer4, layer7, NUMBER_OF_CLASSES)

    # Returns the output logits, training operation and cost operation to be used
    # For the logits: each row represents a pixel, each column a class
    # training operation is what is used to get the right parameters to the model to correctly label the pixels
    # the cross entropy loss is the cost which we are minimizing, lower cost should yield higher accuracy
    logits, train_op, cross_entropy_loss = optimize(model_output, correct_label, learning_rate, NUMBER_OF_CLASSES)
    
    # Initilize all variables
    session.run([tf.global_variables_initializer(), tf.local_variables_initializer()])
    
    # Create saver
    saver = tf.train.Saver()

    # train the neural network
    train_nn(session, EPOCHS, BATCH_SIZE, get_batches_fn, 
             train_op, cross_entropy_loss, image_input,
             correct_label, keep_prob, learning_rate, saver)
    
    # Save inference data
    helper.save_inference_samples(RUNS_DIRECTORY, TESTING_DIRECTORIES, session, IMAGE_SHAPE, logits, keep_prob, image_input)    

In [17]:
def network_shapes():
  with tf.Session() as sess:
    x = np.random.randn(1, 160, 576, 3)
    
    image_input, keep_prob, layer3, layer4, layer7 = load_vgg(sess, VGG_PATH)
 
    op = layers_verbose(layer3, layer4, layer7, NUMBER_OF_CLASSES)
  
    sess.run([tf.global_variables_initializer(), tf.local_variables_initializer()])

    l3, l4, l7, l3x, l4x, l7x, d1, s2, d3, s4, d5 = sess.run(op, feed_dict = {image_input: x, keep_prob: 1.0})

    print("------------------")
    print("shapes of layers:") 
    print("------------------")

    print("layer3 -->", l3.shape)
    print("layer4 -->", l4.shape)
    print("layer7 -->", l7.shape)
    print("layer3 conv1x1 -->", l3x.shape)
    print("layer4 conv1x1 -->", l4x.shape)
    print("layer7 conv1x1-->", l7x.shape)
    print("decoderlayer1 transpose: layer7 k = 4 s = 2 -->", d1.shape)
    print("decoderlayer2 skip: decoderlayer1 and layer4conv1x1 -->", s2.shape)
    print("decoderlayer3 transpose: decoderlayer2 k = 4 s = 2 -->", d3.shape)
    print("decoderlayer4 skip: decoderlayer3 and layer3conv1x1 -->", s4.shape)
    print("decoderlayer5 transpose: decoderlayer4 k = 16 s = 8 -->", d5.shape)

In [18]:
# Train the network
run()

NUMBER OF IMAGES: 13226
INFO:tensorflow:Restoring parameters from b'./data/vgg/variables/variables'
Instructions for updating:

Future major versions of TensorFlow will allow gradients to flow
into the labels input on backprop by default.

See @{tf.nn.softmax_cross_entropy_with_logits_v2}.

---> iteration:  1  partial loss: 43.24416
---> iteration:  2  partial loss: 36.45972
---> iteration:  3  partial loss: 27.47319
---> iteration:  4  partial loss: 20.859596
---> iteration:  5  partial loss: 18.910704
---> iteration:  6  partial loss: 16.168331
---> iteration:  7  partial loss: 13.273679
---> iteration:  8  partial loss: 11.415592
---> iteration:  9  partial loss: 11.04564
---> iteration:  10  partial loss: 9.770063
---> iteration:  11  partial loss: 8.846963
---> iteration:  12  partial loss: 7.6105275
---> iteration:  13  partial loss: 7.236069
---> iteration:  14  partial loss: 6.6515923
---> iteration:  15  partial loss: 6.0262
---> iteration:  16  partial loss: 5.305287
---> ite

---> iteration:  171  partial loss: 0.7380042
---> iteration:  172  partial loss: 0.75620455
---> iteration:  173  partial loss: 0.73579085
---> iteration:  174  partial loss: 0.73494625
---> iteration:  175  partial loss: 0.73396
---> iteration:  176  partial loss: 0.73510355
---> iteration:  177  partial loss: 0.7519622
---> iteration:  178  partial loss: 0.7485718
---> iteration:  179  partial loss: 0.73899144
---> iteration:  180  partial loss: 0.75351614
---> iteration:  181  partial loss: 0.76036793
---> iteration:  182  partial loss: 0.75651115
---> iteration:  183  partial loss: 0.72934395
---> iteration:  184  partial loss: 0.7277556
---> iteration:  185  partial loss: 0.7469054
---> iteration:  186  partial loss: 0.7495372
---> iteration:  187  partial loss: 0.7400232
---> iteration:  188  partial loss: 0.7253938
---> iteration:  189  partial loss: 0.75150645
---> iteration:  190  partial loss: 0.72290564
---> iteration:  191  partial loss: 0.72172695
---> iteration:  192  pa

---> iteration:  348  partial loss: 0.6561238
---> iteration:  349  partial loss: 0.6617741
---> iteration:  350  partial loss: 0.65507317
---> iteration:  351  partial loss: 0.6604438
---> iteration:  352  partial loss: 0.6550471
---> iteration:  353  partial loss: 0.65491813
---> iteration:  354  partial loss: 0.6700602
---> iteration:  355  partial loss: 0.6542482
---> iteration:  356  partial loss: 0.65396374
---> iteration:  357  partial loss: 0.6531364
---> iteration:  358  partial loss: 0.6529184
---> iteration:  359  partial loss: 0.65847564
---> iteration:  360  partial loss: 0.6608648
---> iteration:  361  partial loss: 0.6525794
---> iteration:  362  partial loss: 0.651573
---> iteration:  363  partial loss: 0.65730584
---> iteration:  364  partial loss: 0.65540606
---> iteration:  365  partial loss: 0.65719736
---> iteration:  366  partial loss: 0.65978116
---> iteration:  367  partial loss: 0.6498933
---> iteration:  368  partial loss: 0.64972186
---> iteration:  369  part

---> iteration:  525  partial loss: 0.58785135
---> iteration:  526  partial loss: 0.5833277
---> iteration:  527  partial loss: 0.5847163
---> iteration:  528  partial loss: 0.5832558
---> iteration:  529  partial loss: 0.5774215
---> iteration:  530  partial loss: 0.58105975
---> iteration:  531  partial loss: 0.5838619
---> iteration:  532  partial loss: 0.5756177
---> iteration:  533  partial loss: 0.57819694
---> iteration:  534  partial loss: 0.573116
---> iteration:  535  partial loss: 0.5774959
---> iteration:  536  partial loss: 0.5843127
---> iteration:  537  partial loss: 0.57128894
---> iteration:  538  partial loss: 0.5692231
---> iteration:  539  partial loss: 0.57656485
---> iteration:  540  partial loss: 0.5742167
---> iteration:  541  partial loss: 0.5724936
---> iteration:  542  partial loss: 0.56625396
---> iteration:  543  partial loss: 0.5638724
---> iteration:  544  partial loss: 0.5642737
---> iteration:  545  partial loss: 0.5630176
---> iteration:  546  partial

---> iteration:  701  partial loss: 0.34791133
---> iteration:  702  partial loss: 0.31340158
---> iteration:  703  partial loss: 0.3277627
---> iteration:  704  partial loss: 0.30528533
---> iteration:  705  partial loss: 0.32328135
---> iteration:  706  partial loss: 0.32184142
---> iteration:  707  partial loss: 0.2980566
---> iteration:  708  partial loss: 0.32207456
---> iteration:  709  partial loss: 0.3124585
---> iteration:  710  partial loss: 0.30343673
---> iteration:  711  partial loss: 0.32806927
---> iteration:  712  partial loss: 0.30520415
---> iteration:  713  partial loss: 0.30437297
---> iteration:  714  partial loss: 0.30002737
---> iteration:  715  partial loss: 0.2978725
---> iteration:  716  partial loss: 0.2769775
---> iteration:  717  partial loss: 0.32289815
---> iteration:  718  partial loss: 0.31750032
---> iteration:  719  partial loss: 0.2826715
---> iteration:  720  partial loss: 0.28691128
---> iteration:  721  partial loss: 0.28048924
---> iteration:  72

...

---> iteration:  12508  partial loss: 1.02462764e-07
---> iteration:  12509  partial loss: 3.6282138e-08
---> iteration:  12510  partial loss: 5.8323906e-08
---> iteration:  12511  partial loss: 1.9575175e-08
---> iteration:  12512  partial loss: 7.1018526e-08
---> iteration:  12513  partial loss: 6.5348246e-08
---> iteration:  12514  partial loss: 5.983453e-08
---> iteration:  12515  partial loss: 8.510616e-08
---> iteration:  12516  partial loss: 4.1858765e-08
---> iteration:  12517  partial loss: 5.160146e-08
---> iteration:  12518  partial loss: 8.352403e-08
---> iteration:  12519  partial loss: 4.9046847e-08
---> iteration:  12520  partial loss: 6.0803806e-08
---> iteration:  12521  partial loss: 5.168155e-08
---> iteration:  12522  partial loss: 9.686521e-07
---> iteration:  12523  partial loss: 7.8044714e-08
---> iteration:  12524  partial loss: 9.0077826e-08
---> iteration:  12525  partial loss: 6.147171e-08
---> iteration:  12526  partial loss: 7.2525694e-08
---> iteration:  1

---> iteration:  12667  partial loss: 4.085488e-08
---> iteration:  12668  partial loss: 4.282355e-08
---> iteration:  12669  partial loss: 4.3529255e-08
---> iteration:  12670  partial loss: 3.98231e-08
---> iteration:  12671  partial loss: 2.515021e-08
---> iteration:  12672  partial loss: 3.1577446e-08
---> iteration:  12673  partial loss: 1.1192114e-06
---> iteration:  12674  partial loss: 1.6589043e-07
---> iteration:  12675  partial loss: 3.6660825e-08
---> iteration:  12676  partial loss: 2.6646916e-08
---> iteration:  12677  partial loss: 2.618935e-08
---> iteration:  12678  partial loss: 5.5297022e-08
---> iteration:  12679  partial loss: 1.403887e-08
---> iteration:  12680  partial loss: 5.670133e-08
---> iteration:  12681  partial loss: 1.6140145e-08
---> iteration:  12682  partial loss: 3.5459866e-08
---> iteration:  12683  partial loss: 4.1155502e-08
---> iteration:  12684  partial loss: 4.2265427e-08
---> iteration:  12685  partial loss: 8.8301206e-08
---> iteration:  126

---> iteration:  12828  partial loss: 1.2251153e-05
---> iteration:  12829  partial loss: 0.0112093035
---> iteration:  12830  partial loss: 0.010847607
---> iteration:  12831  partial loss: 0.0062038573
---> iteration:  12832  partial loss: 1.0152442e-05
---> iteration:  12833  partial loss: 0.003933755
---> iteration:  12834  partial loss: 0.00951307
---> iteration:  12835  partial loss: 9.544858e-06
---> iteration:  12836  partial loss: 0.006838498
---> iteration:  12837  partial loss: 0.008705244
---> iteration:  12838  partial loss: 0.007860354
---> iteration:  12839  partial loss: 0.010250933
---> iteration:  12840  partial loss: 0.007307965
---> iteration:  12841  partial loss: 0.0076216045
---> iteration:  12842  partial loss: 0.0036706524
---> iteration:  12843  partial loss: 6.5502027e-06
---> iteration:  12844  partial loss: 0.0081801005
---> iteration:  12845  partial loss: 0.010744677
---> iteration:  12846  partial loss: 0.010383464
---> iteration:  12847  partial loss: 0

---> iteration:  12990  partial loss: 0.0072822864
---> iteration:  12991  partial loss: 0.0007324805
---> iteration:  12992  partial loss: 0.007550227
---> iteration:  12993  partial loss: 0.0035375566
---> iteration:  12994  partial loss: 0.0007299109
---> iteration:  12995  partial loss: 0.007413527
---> iteration:  12996  partial loss: 1.1523216e-06
---> iteration:  12997  partial loss: 0.00414875
---> iteration:  12998  partial loss: 0.0074966485
---> iteration:  12999  partial loss: 8.2225614e-07
---> iteration:  13000  partial loss: 0.0067217685
---> iteration:  13001  partial loss: 3.470135e-06
---> iteration:  13002  partial loss: 0.000706019
---> iteration:  13003  partial loss: 0.007721634
---> iteration:  13004  partial loss: 4.800483e-07
---> iteration:  13005  partial loss: 0.0115049
---> iteration:  13006  partial loss: 0.008755193
---> iteration:  13007  partial loss: 0.010110012
---> iteration:  13008  partial loss: 0.00023501476
---> iteration:  13009  partial loss: 0

---> iteration:  13152  partial loss: 0.0043358766
---> iteration:  13153  partial loss: 0.00062244706
---> iteration:  13154  partial loss: 4.816338e-07
---> iteration:  13155  partial loss: 5.9481437e-07
---> iteration:  13156  partial loss: 0.00054555316
---> iteration:  13157  partial loss: 0.00666811
---> iteration:  13158  partial loss: 0.005714736
---> iteration:  13159  partial loss: 0.006279963
---> iteration:  13160  partial loss: 0.0016750161
---> iteration:  13161  partial loss: 4.5744747e-07
---> iteration:  13162  partial loss: 8.8801704e-07
---> iteration:  13163  partial loss: 0.011690048
---> iteration:  13164  partial loss: 0.008231433
---> iteration:  13165  partial loss: 1.222872e-06
---> iteration:  13166  partial loss: 0.0064933784
---> iteration:  13167  partial loss: 0.009842198
---> iteration:  13168  partial loss: 9.0190166e-05
---> iteration:  13169  partial loss: 0.0053265193
---> iteration:  13170  partial loss: 0.00042344927
---> iteration:  13171  partial

In [19]:
all_training_losses

[0.07343140707652739,
 0.008481552011448887,
 0.007005867444308261,
 0.005339318504487202,
 0.004044123621170448,
 0.003348009735311531,
 0.003001293968142109,
 0.0025795786097878256,
 0.002296257664773849,
 0.0020684018605577072]

In [20]:
tf.reset_default_graph()
    
with tf.Session() as session:
    # Restore variables and model
    saver = tf.train.import_meta_graph("./model.ckpt.meta")
    print("Model restored.")
    
   
    # Get the three layers, keep probability and input layer
    graph = tf.get_default_graph()
    image_input = graph.get_tensor_by_name('image_input:0')
    keep_prob = graph.get_tensor_by_name('keep_prob:0')
    layer3 = graph.get_tensor_by_name('layer3_out:0')
    layer4 = graph.get_tensor_by_name('layer4_out:0')
    layer7 = graph.get_tensor_by_name('layer7_out:0')

    # The resulting network architecture, adding a decoder on top of the given vgg model
    model_output = layers(layer3, layer4, layer7, NUMBER_OF_CLASSES)

    logits = tf.reshape(model_output, (-1, NUMBER_OF_CLASSES))
    print('Graph constructed')
    
    # Initilize all variables
    session.run([tf.global_variables_initializer(), tf.local_variables_initializer()])
    print('Variables initialized')
    
    # Restore variables that were trained from previous session
    saver.restore(session, tf.train.latest_checkpoint("./"))
    
    # TEST IMAGE
    test_image = scipy.misc.imresize(scipy.misc.imread("./data/data_liquid/testing/image_2/data0257.png"), IMAGE_SHAPE)
    
    # Make predictions
    feed = {keep_prob: 1.0, image_input: [test_image]}
    im_softmax = session.run( [tf.nn.softmax(logits)], feed)
    im_softmax = im_softmax[0][:, 1].reshape(IMAGE_SHAPE[0], IMAGE_SHAPE[1])
    segmentation = (im_softmax > 0.5).reshape(IMAGE_SHAPE[0], IMAGE_SHAPE[1], 1)
    mask = np.dot(segmentation, np.array([[0, 255, 0, 127]]))
    mask = scipy.misc.toimage(mask, mode="RGBA")
    result = scipy.misc.toimage(test_image)
    result.paste(mask, box=None, mask=mask)
    plt.imshow(result)
    plt.show()  
   
    
    #helper.save_inference_samples(RUNS_DIRECTORY, DATA_DIRECTORY, session, IMAGE_SHAPE, logits, keep_prob, image_input)

Model restored.
Graph constructed
Variables initialized
INFO:tensorflow:Restoring parameters from ./model_10epochs


/home/gother/.local/lib/python3.5/site-packages/ipykernel_launcher.py:31: DeprecationWarning: `imread` is deprecated!
`imread` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``imageio.imread`` instead.


FileNotFoundError: [Errno 2] No such file or directory: './data/data_liquid/testing/image_2/data0257.png'

In [ ]:
def run_tests():
  print("NUMBER OF IMAGES:", NUMBER_OF_IMAGES)

  # download vgg model
  helper.maybe_download_pretrained_vgg(DATA_DIRECTORY)

  # A function to get batches
  get_batches_fn = helper.gen_batch_function(TRAINING_DATA_DIRECTORY, IMAGE_SHAPE)
  tf.reset_default_graph()
   
  with tf.Session() as session:
    
    # Restore variables and model
    saver = tf.train.import_meta_graph("./fcn_liquid_model-500.meta")
    saver.restore(session, tf.train.latest_checkpoint("./"))
    print("Model restored.")
    
     # Initilize all variables
    session.run([tf.global_variables_initializer(), tf.local_variables_initializer()])
        
    # load the model and weights
    model = tf.saved_model.loader.load(session, ['vgg16'], VGG_PATH)

    # Get Tensors to be returned from graph
    graph = tf.get_default_graph()
    image_input = graph.get_tensor_by_name('image_input:0')
    keep_prob = graph.get_tensor_by_name('keep_prob:0')
    layer3 = graph.get_tensor_by_name('layer3_out:0')
    layer4 = graph.get_tensor_by_name('layer4_out:0')
    layer7 = graph.get_tensor_by_name('layer7_out:0')
    class_labels = tf.reshape(correct_label, (-1, NUMBER_OF_CLASSES))

    # The resulting network architecture, adding a decoder on top of the given vgg model
    model_output = layers(layer3, layer4, layer7, NUMBER_OF_CLASSES)
    
    # reshape 4D tensors to 2D
    # Each row represents a pixel, each column a class
    logits = tf.reshape(model_output, (-1, NUMBER_OF_CLASSES))
   

    # The cross_entropy_loss is the cost which we are trying to minimize to yield higher accuracy
    #cross_entropy = tf.nn.softmax_cross_entropy_with_logits(logits = logits, labels = class_labels)
    #cross_entropy_loss = tf.reduce_mean(cross_entropy)

    # The model implements this operation to find the weights/parameters that would yield correct pixel labels
    #train_op = tf.train.AdamOptimizer(learning_rate).minimize(cross_entropy_loss)    
    
    # TEST IMAGE
    test_image = scipy.misc.imresize(scipy.misc.imread("./data/data_liquid/testing/image_2/data0257.png"), IMAGE_SHAPE)
    
    im_softmax = session.run(
            [tf.nn.softmax(logits)],
            {keep_prob: 1.0, image_input: [test_image]})
    """
    im_softmax = im_softmax[0][:, 1].reshape(IMAGE_SHAPE[0], IMAGE_SHAPE[1])
    segmentation = (im_softmax > 0.5).reshape(IMAGE_SHAPE[0], IMAGE_SHAPE[1], 1)
    mask = np.dot(segmentation, np.array([[0, 255, 0, 127]]))
    mask = scipy.misc.toimage(mask, mode="RGBA")
    result = scipy.misc.toimage(test_image)
    result.paste(mask, box=None, mask=mask)
    plt.imshow(result)
    plt.show() """
   
    # Save inference data
    #helper.save_inference_samples(RUNS_DIRECTORY, DATA_DIRECTORY, session, IMAGE_SHAPE, logits, keep_prob, image_input)    

In [ ]:
[n.name for n in tf.get_default_graph().as_graph_def().node]

In [ ]:
def run_traintest():
  print("NUMBER OF IMAGES:", NUMBER_OF_IMAGES)

  # download vgg model
  helper.maybe_download_pretrained_vgg(DATA_DIRECTORY)

  # A function to get batches
  get_batches_fn = helper.gen_batch_function(TRAINING_DIRECTORIES, IMAGE_SHAPE)

 
  
  with tf.Session() as session:
        
    # Returns the three layers, keep probability and input layer from the vgg architecture
    image_input, keep_prob, layer3, layer4, layer7 = load_vgg(session, VGG_PATH)

    # The resulting network architecture, adding a decoder on top of the given vgg model
    model_output = layers(layer3, layer4, layer7, NUMBER_OF_CLASSES)

    # Returns the output logits, training operation and cost operation to be used
    # For the logits: each row represents a pixel, each column a class
    # training operation is what is used to get the right parameters to the model to correctly label the pixels
    # the cross entropy loss is the cost which we are minimizing, lower cost should yield higher accuracy
    logits, train_op, cross_entropy_loss = optimize(model_output, correct_label, learning_rate, NUMBER_OF_CLASSES)
    
    # Create saver
    saver = tf.train.Saver()
    
    # Initilize all variables
    session.run([tf.global_variables_initializer(), tf.local_variables_initializer()])

    # train the neural network
    train_nn(session, EPOCHS, BATCH_SIZE, get_batches_fn, 
             train_op, cross_entropy_loss, image_input,
             correct_label, keep_prob, learning_rate)
    
    # Save inference data
    helper.save_inference_samples(RUNS_DIRECTORY, DATA_DIRECTORY, session, IMAGE_SHAPE, logits, keep_prob, image_input)    
    
    # Save model
    saver.save(session, "./fcn_liquid_model", global_step = 500)

In [ ]:
tf.reset_default_graph()

with tf.Session() as session:
    # Restore model graph
    saver = tf.train.import_meta_graph("./model.ckpt.meta")

    # Get the three layers, keep probability and input layer
    graph = tf.get_default_graph()
    image_input = graph.get_tensor_by_name('image_input:0')
    keep_prob = graph.get_tensor_by_name('keep_prob:0')
    layer3 = graph.get_tensor_by_name('layer3_out:0')
    layer4 = graph.get_tensor_by_name('layer4_out:0')
    layer7 = graph.get_tensor_by_name('layer7_out:0')

    # The resulting network architecture, adding a decoder on top of the given vgg model
    model_output = layers(layer3, layer4, layer7, NUMBER_OF_CLASSES)
    logits = tf.reshape(model_output, (-1, NUMBER_OF_CLASSES))
    print('Graph constructed')

	# Initialize all variables
    session.run([tf.global_variables_initializer(), tf.local_variables_initializer()])
    print('Variables initialized')

    # Restore variables that were trained from previous session (a subset of all global & local variables).
    saver.restore(session, tf.train.latest_checkpoint("./"))
    print("Trained Variables restored from previous session.")
    
    print([n.name for n in tf.get_default_graph().as_graph_def().node])

    # load image
    test_image = scipy.misc.imresize(scipy.misc.imread("./data/data_liquid/testing/image_2/data0257.png"), IMAGE_SHAPE)

    # Make predictions
    feed = {keep_prob: 1.0, image_input: [test_image]}
    im_softmax = session.run( [tf.nn.softmax(logits)], feed)
    im_softmax = im_softmax[0][:, 1].reshape(IMAGE_SHAPE[0], IMAGE_SHAPE[1])
    segmentation = (im_softmax > 0.5).reshape(IMAGE_SHAPE[0], IMAGE_SHAPE[1], 1)
    mask = np.dot(segmentation, np.array([[0, 255, 0, 127]]))
    mask = scipy.misc.toimage(mask, mode="RGBA")
    result = scipy.misc.toimage(test_image)
    result.paste(mask, box=None, mask=mask)
    plt.imshow(result)
    plt.show()

In [ ]:
from glob import glob
import re

directory = "./data/data_liquid/training"
dirs = [x[0] for x in os.walk(directory)]
#print(dirs[1:])
dirs = dirs[1:]

image_paths = glob(os.path.join(TRAINING_DATA_DIRECTORY, 'image_2', '*.png'))
#print(image_paths)

x = 0
for d in dirs:
    ip = glob(os.path.join(d, 'data*.png'))
    x += len(ip)

print(x)
#print(ip)

if image_paths == ip:
    print("Yes")
else:
    print("No")

label_paths = {
                re.sub(r'ground_truth', 'data', os.path.basename(path)): path
                for path in glob(os.path.join(TRAINING_DATA_DIRECTORY, 'gt_image_2', '*.png'))}

#print(label_paths)


lp = {
       re.sub(r'ground_truth', 'data', os.path.basename(path)): path
       for path in glob(os.path.join(dirs[1], 'ground_truth*.png'))}

print(lp)



if label_paths == lp:
    print("Yes")
else:
    print("No")